In [ ]:
pwd

In [ ]:
import torch
from torch import nn, optim
import os
from torchvision import models
import config
import numpy as np
import random
from torch.utils.data import DataLoader
from tqdm import tqdm
from sklearn.metrics import cohen_kappa_score
from efficientnet_pytorch import EfficientNet
from dataset import DRDataset
import datetime
from torchvision.utils import save_image
from earlystopper import EarlyStopper
import csv 
from utils import (
    load_checkpoint,
    save_checkpoint,
    check_accuracy,
    make_prediction,
    get_csv_for_blend,
)

In [ ]:
def set_seed(seed: int = 42) -> None:
    np.random.seed(seed)
    random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    # When running on the CuDNN backend, two further options must be set
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False
    # Set a fixed value for the hash seed
    os.environ["PYTHONHASHSEED"] = str(seed)
    print(f"Random seed set as {seed}")


# Set a specific seed value (you can use any integer)
seed = 42
set_seed(seed)

In [ ]:
def train_one_epoch(loader, model, optimizer, loss_fn, scaler, device):
    losses = []
    loop = tqdm(loader)
    for batch_idx, (data, targets, _) in enumerate(loop):
        # save examples and make sure they look ok with the data augmentation,
        # tip is to first set mean=[0,0,0], std=[1,1,1] so they look "normal"
        #save_image(data, f"hi_{batch_idx}.png")

        data = data.to(device=device)
        #print(data.shape)
        #print("Targets",targets)
        targets = targets.to(device=device)

        # forward
        with torch.cuda.amp.autocast():
            scores = model(data)
            loss = loss_fn(scores, targets.unsqueeze(1).float())

        losses.append(loss.item())

        # backward
        optimizer.zero_grad()
        scaler.scale(loss).backward()
        scaler.step(optimizer)
        scaler.update()
        loop.set_postfix(loss=loss.item())

    print(f"Loss average over epoch: {sum(losses)/len(losses)}")

In [ ]:
hyperparameter_combinations = [
{'batch_size': 64, 'learning_rate': 0.0002, 'epochs': 700},
{'batch_size': 64, 'learning_rate': 2e-05, 'epochs': 700},
{'batch_size': 64, 'learning_rate': 0.005, 'epochs': 700},
{'batch_size': 64, 'learning_rate': 0.0005, 'epochs': 700},
{'batch_size': 64, 'learning_rate': 5e-05, 'epochs': 700},
{'batch_size': 64, 'learning_rate': 0.003, 'epochs': 700},
{'batch_size': 64, 'learning_rate': 0.0003, 'epochs': 700},
{'batch_size': 64, 'learning_rate': 3e-05, 'epochs': 700},
{'batch_size': 64, 'learning_rate': 0.001, 'epochs': 700},
{'batch_size': 64, 'learning_rate': 0.0001, 'epochs': 700},
{'batch_size': 64, 'learning_rate': 1e-05, 'epochs': 700},
{'batch_size': 32, 'learning_rate': 0.002, 'epochs': 700},
{'batch_size': 32, 'learning_rate': 0.0002, 'epochs': 700},
{'batch_size': 32, 'learning_rate': 2e-05, 'epochs': 700},
{'batch_size': 32, 'learning_rate': 0.005, 'epochs': 700},
{'batch_size': 32, 'learning_rate': 0.0005, 'epochs': 700},
{'batch_size': 32, 'learning_rate': 5e-05, 'epochs': 700},
{'batch_size': 32, 'learning_rate': 0.003, 'epochs': 700},
{'batch_size': 32, 'learning_rate': 0.0003, 'epochs': 700},
{'batch_size': 32, 'learning_rate': 3e-05, 'epochs': 700},
{'batch_size': 32, 'learning_rate': 0.001, 'epochs': 700},
{'batch_size': 32, 'learning_rate': 0.0001, 'epochs': 700},
{'batch_size': 32, 'learning_rate': 1e-05, 'epochs': 700},
]
#131,64,3e-05,0,82.90636042402826,78.10476751030018,0

In [ ]:
import os
import datetime
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader
from torchvision import models
from sklearn.metrics import cohen_kappa_score

def training_main(hyperparams, early_stopper):
    BATCH_SIZE = hyperparams['batch_size']
    LEARNING_RATE = hyperparams['learning_rate']
    NUM_EPOCHS = hyperparams['epochs']
    
    best_accuracy = 0.0
    best_precision = 0.0
    best_recall = 0.0
    best_train_accuracy = 0.0
    best_f1 = 0.0
    best_train_precision = 0.0
    best_train_recall = 0.0
    best_train_f1 = 0.0
        
    current_time = datetime.datetime.now().strftime("%Y%m%d_%H%M%S")
    output_folder = f"output_results/ResNet50_RS_training_{current_time}_{BATCH_SIZE}_{LEARNING_RATE}"
    os.makedirs(output_folder)
    
    train_ds = DRDataset(
        images_folder="/home/shashank/All_code/Research/APTOS_dataset/aptos2019_blindness_detection/Real_Synthetic/RS_train_split",
        path_to_csv="/home/shashank/All_code/Research/APTOS_dataset/aptos2019_blindness_detection/Real_Synthetic/RS_train_split.csv",
        transform=config.val_transforms,
    )
    val_ds = DRDataset(
        images_folder="/home/shashank/All_code/Research/APTOS_dataset/aptos2019_blindness_detection/Real_Synthetic/RS_val_split",
        path_to_csv="/home/shashank/All_code/Research/APTOS_dataset/aptos2019_blindness_detection/Real_Synthetic/RS_val_split.csv",
        transform=config.val_transforms,
    )
    test_ds = DRDataset(
        images_folder="/home/shashank/All_code/test/images_resized_192",
        path_to_csv="/home/shashank/All_code/Research/APTOS_dataset/aptos2019_blindness_detection/test.csv",
        transform=config.val_transforms,
        train=False,
    )
    test_loader = DataLoader(
        test_ds, batch_size=BATCH_SIZE, num_workers=6, shuffle=False
    )
    train_loader = DataLoader(
        train_ds,
        batch_size=BATCH_SIZE,
        num_workers=config.NUM_WORKERS,
        pin_memory=config.PIN_MEMORY,
        shuffle=False,
    )
    val_loader = DataLoader(
        val_ds,
        batch_size=BATCH_SIZE,
        num_workers=config.NUM_WORKERS, 
        pin_memory=config.PIN_MEMORY,
        shuffle=False,
    )
    
    loss_fn = nn.MSELoss()
    
    model = models.resnet50(pretrained=True)
    model.fc = nn.Linear(model.fc.in_features, 1)
    model = model.to(config.DEVICE)
    
    optimizer = optim.Adam(model.parameters(), lr=LEARNING_RATE, weight_decay=config.WEIGHT_DECAY)
    scaler = torch.cuda.amp.GradScaler()

    print("OS Path ", os.listdir())    
    if config.LOAD_MODEL and config.CHECKPOINT_FILE in os.listdir():
        load_checkpoint(torch.load(config.CHECKPOINT_FILE), model, optimizer, LEARNING_RATE)
        print("Model Loaded !!!!!!!!")

    for epoch in range(NUM_EPOCHS):
        print("Epoch - ", epoch)
        train_one_epoch(train_loader, model, optimizer, loss_fn, scaler, config.DEVICE)

        # get on validation
        preds, labels, val_accuracy, val_precision, val_recall, val_f1 = check_accuracy(val_loader, model, config.DEVICE)
        quad_score_val = cohen_kappa_score(labels, preds, weights='quadratic')
        print(f"QuadraticWeightedKappa (Validation): ", quad_score_val)
        
        # get on train
        preds, labels, train_accuracy, train_precision, train_recall, train_f1 = check_accuracy(train_loader, model, config.DEVICE)
        quad_score_train = cohen_kappa_score(labels, preds, weights='quadratic')
        print(f"QuadraticWeightedKappa (Training): {quad_score_train}")

        if val_accuracy > best_accuracy:
            best_train_accuracy = train_accuracy
            best_accuracy = val_accuracy
            epoch_checkpoint = epoch + 1
            
        if val_precision > best_precision:
            best_train_precision = train_precision
            best_precision = val_precision
            
        if val_recall > best_recall:
            best_train_recall = train_recall
            best_recall = val_recall
            
        if val_f1 > best_f1:
            best_train_f1 = train_f1
            best_f1 = val_f1
            print()

        if config.SAVE_MODEL:
            checkpoint = {
                "state_dict": model.state_dict(),
                "optimizer": optimizer.state_dict(),
            }
            save_checkpoint(checkpoint, filename=os.path.join(output_folder, "resnet50_checkpoint.pth.tar"))

        if early_stopper.early_stop(val_accuracy):
            print("Early stopping triggered!")
            break

    return epoch, best_accuracy, best_train_accuracy, best_train_precision, best_train_recall, best_train_f1, best_precision, best_recall, best_f1, quad_score_val


In [7]:
current_time = datetime.datetime.now().strftime("%Y%m%d_%H%M%S")
log_file = os.path.join("/home/shashank/All_code/Research/APTOS_Detection/output_results", f"{current_time}_ResNet50_192_REALSYNTH_log.csv")
with open(log_file, 'w', newline='') as csvfile:
    fieldnames = ['epoch','batch_size','Learning_rate', 'training_loss', 'training_accuracy',
                  'train_precision','train_recall','train_f1','val_accuracy', 'val_loss','val_precision','val_recall','val_f1','Qudratic_kappa_score_val']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
    writer.writeheader()

for hyperparams in hyperparameter_combinations:
    torch.cuda.empty_cache()
    # Instantiate EarlyStopper with desired patience and min_delta
    early_stopper = EarlyStopper(patience=60, min_delta=0.001)
    print("hyperparameter_combinations >>>>>>>>>>>>>> ",hyperparams)
    epoch , best_accuracy,best_train_accuracy,best_train_precision,best_train_recall,best_train_f1, best_precision, best_recall, best_f1,quad_score_val = training_main(hyperparams,early_stopper)
    

    with open(log_file, 'a', newline='') as csvfile:
        writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
        writer.writerow({
            'epoch': epoch,
            'batch_size': hyperparams['batch_size'],
            'Learning_rate': hyperparams['learning_rate'],
            'training_loss': "0",
            'training_accuracy': best_train_accuracy,
            'train_precision' : best_train_precision,
            'train_recall' : best_train_recall,
            'train_f1' : best_train_f1,
            
            'val_accuracy': best_accuracy,
            'val_loss' : "0",
            'val_precision' : best_precision,
            'val_recall' : best_recall,
            'val_f1' : best_f1,
            'Qudratic_kappa_score_val': quad_score_val,
            
                })

100%|██████████| 52/52 [00:01<00:00, 28.74it/s, loss=0.00936]


Loss average over epoch: 0.02200237458321051


100%|██████████| 6/6 [00:00<00:00, 21.60it/s]


Got 282 / 367 with accuracy 76.84
Shapes - all_preds: (367,) all_labels: (367,)
DataType - all_preds: int64 all_labels: int64
Unique labels: [0 1 2 3 4]
Accuracy: 76.84
Precision: 0.80
Recall: 0.77
F1 Score: 0.77
QuadraticWeightedKappa (Validation):  0.8788978716383435


100%|██████████| 52/52 [00:01<00:00, 29.23it/s]


...

Loss average over epoch: 0.010499566009051158


100%|██████████| 12/12 [00:00<00:00, 46.29it/s]


Got 282 / 367 with accuracy 76.84
Shapes - all_preds: (367,) all_labels: (367,)
DataType - all_preds: int64 all_labels: int64
Unique labels: [0 1 2 3 4]
Accuracy: 76.84
Precision: 0.80
Recall: 0.77
F1 Score: 0.76
QuadraticWeightedKappa (Validation):  0.8749257539021802


100%|██████████| 103/103 [00:01<00:00, 58.84it/s]


Got 3201 / 3295 with accuracy 97.15
Shapes - all_preds: (3295,) all_labels: (3295,)
DataType - all_preds: int64 all_labels: int64
Unique labels: [0 1 2 3 4]
Accuracy: 97.15
Precision: 0.98
Recall: 0.97
F1 Score: 0.97
QuadraticWeightedKappa (Training): 0.9908472684943649
=> Saving checkpoint
Early stopping triggered!
